**Table of contents**<a id='toc0_'></a>    
- [Pass text through model for attention](#toc1_)    
- [BERT Attention Visualization](#toc2_)    
- [Transformer-Interpret](#toc3_)    
- [LIME](#toc4_)    
- [BERTViz](#toc5_)    

<!-- vscode-jupyter-toc-config
	numbering=false
	anchor=true
	flat=false
	minLevel=1
	maxLevel=6
	/vscode-jupyter-toc-config -->
<!-- THIS CELL WILL BE REPLACED ON TOC UPDATE. DO NOT WRITE YOUR TEXT IN THIS CELL -->

In [3]:
DATA_PATH = "/home1/vnguyen2014/IRI/umd"
MODEL_PATH = "/home1/vnguyen2014/IRI/models"


# <a id='toc1_'></a>[Pass text through model for attention](#toc0_)

In [4]:
import pandas as pd
df = pd.read_parquet(f"{DATA_PATH}/test.parquet.gzip")

print(df.loc[200])

print(df.loc[200].text)

text     I had the gun in my mouth pointed, I think, at...
label                                                    3
Name: 200, dtype: object
I had the gun in my mouth pointed, I think, at my brain stem. I had both index fingers on the trigger and I wanted to pull harder. I don't know why but I couldn't. I was breathing so hard. I feel so scared. I don't know what I'm going to do. I guess I have to face another week somehow. I put my laundry in the wash. I don't know what I'm doing anymore. Maybe I'll try and seal a plastic bag over my head instead. It's less violent and its not something I have to actively do. I can just lay there. I don't know what I'm going to do. I don't think I can handle another week. I'm so done. I had my last therapist appointment today. She told me that while she doesn't want me to die, and she wishes I'd give more time to doctors and meds and whatever. I don't have the energy or the will for that anymore. I just can't. I'm so tired. I have to be done. I just

In [5]:
import torch
from transformers import AutoTokenizer, AutoModelForSequenceClassification

# Load the pre-trained and fine-tuned model
model_path = f"{MODEL_PATH}/mental/mental-roberta-base"
model_name = "mental/mental-roberta-base"
model = AutoModelForSequenceClassification.from_pretrained(model_path,output_attentions=True, output_hidden_states=True)

# Make sure the model is in evaluation mode
model.eval()

# Load the tokenizer
tokenizer = AutoTokenizer.from_pretrained(model_name)

# Input text for visualization
input_text = df.loc[200].text
# input_text = "I had the gun in my mouth pointed, I think, at my brain stem. I had both index fingers on the trigger and I wanted to pull harder. I don't know why but I couldn't. I was breathing so hard. I feel so scared"

# Tokenize the input text
inputs = tokenizer.encode(input_text, return_tensors="pt")

# Get the attention weights from the last layer
with torch.no_grad():
    outputs = model(inputs)
    last_layer_attentions = outputs.attentions[-1]  # Shape: (num_heads, seq_len, seq_len)

# Move the attention weights to the CPU and convert to NumPy array
last_layer_attentions = last_layer_attentions.squeeze(0).cpu().numpy()


# <a id='toc2_'></a>[BERT Attention Visualization](#toc0_)

In [99]:
from xml.etree.ElementTree import Element, SubElement, tostring
import numpy as np
def viz_attention(tokens, token_weights, target_label, pred_probs, review_id, viz_relative=None):
    """
    Returns a html string with the tokens highlighted according to its weights
    :param tokens: A list of strings
    :param token_weights: A rank 1 numpy array where each element is the weight to attach to the corresponding token
    :param target_label: The input's ground truth label
    :param pred_label: The predicted label
    :param pred_probs: The array of predicted probabilities
    :param review_id: The input's id
    :param viz_relative: boolean indicating whether to normalize token_weights by dividing it by the max weight
    :return: A html string
    """
    # clean up tokens
    tokens = [token.replace('Ġ', ' ') for token in tokens]
    # remove special tokens
    tokens = tokens[1:-1]
    token_weights = token_weights[1:-1]

    # minmax scale
    if viz_relative=="minmax":
        token_weights = (token_weights - torch.min(token_weights)) / (torch.max(token_weights) - torch.min(token_weights)) if viz_relative else token_weights
    elif viz_relative=="maxscale":
        token_weights = token_weights / torch.max(token_weights)
    else:
        token_weights = token_weights
    pred_label = np.argmax(pred_probs)

    top = Element('span')
    top.set('style', 'white-space: pre-wrap;')

    title = SubElement(top, 'h3')
    title.text = review_id

    header = SubElement(top, 'p')
    header.set('style', 'white-space: pre-line')
    header.text = f"""
    Target label: {target_label}
    Predicted label: {pred_label}
    Probabilities: {pred_probs}
    """

    input_text = SubElement(top, 'p')
    for token, weight in zip(tokens, token_weights):
        child = SubElement(input_text, 'span')
        child.set('style', 'background-color: rgba(0, 0, 256, {})'.format(weight))
        child.text = token
        child.tail = ' '
    
    return tostring(top).decode()

In [ ]:
from IPython.display import HTML

In [98]:
def vis(viz_relative):
    tokens = tokenizer.convert_ids_to_tokens(inputs[0])
    token_weights = torch.mean(outputs.hidden_states[-1][0], dim=1)
    viz = viz_attention(tokens,token_weights,df.loc[200].label,outputs.logits[0],"text1",viz_relative=viz_relative)
    return viz

In [103]:
tokens = tokenizer.convert_ids_to_tokens(inputs[0])

### Last hidden state average

In [105]:
HTML(viz_attention(tokens,torch.mean(outputs.hidden_states[-1][0], dim=1),df.loc[200].label,outputs.logits[0],"text1",viz_relative="minmax"))

### Last attention layer, average across heads and across tokens

In [111]:
HTML(viz_attention(tokens,torch.mean(outputs.attentions[-1][0], dim=(0,1)),df.loc[200].label,outputs.logits[0],"text1",viz_relative="minmax"))

### First attention layer, average across heads and across tokens

In [119]:
HTML(viz_attention(tokens,torch.mean(outputs.attentions[0][0], dim=(0,1)),df.loc[200].label,outputs.logits[0],"text1",viz_relative="minmax"))

# <a id='toc3_'></a>[Transformer-Interpret](#toc0_)

In [6]:
from transformers_interpret import SequenceClassificationExplainer,MultiLabelClassificationExplainer

In [7]:
model.config.id2label = {0:'No Risk',1:'Low Risk',2:'Moderate Risk',3:'Severe Risk'}
model.config.label2id = {"LABEL_0":0,"LABEL_1":1,"LABEL_2":2,"LABEL_3":3}

In [63]:
cls_explainer = MultiLabelClassificationExplainer(model,tokenizer)

In [39]:
import matplotlib.pyplot as plt
from collections import defaultdict
import numpy as np

In [57]:
def gather_word_attributions(word_attributions_result, word_attributions_dict):
    for label,word_attributions in word_attributions_result.items():
        for i in range(len(word_attributions)):
            word_attributions_dict[word_attributions[i][0].lower()][label].append(word_attributions[i][1])
    return word_attributions_dict

In [65]:
word_attributions_dict = defaultdict(lambda: defaultdict(list))
# word_attributions_dict = gather_word_attributions(word_attributions, word_attributions_dict)

In [66]:
for text in df.text:
    word_attributions = cls_explainer(text)
    word_attributions_dict = gather_word_attributions(word_attributions, word_attributions_dict)

KeyboardInterrupt: 

In [61]:
def plot_word_attributions(word_attributions_dict, word):
    bins = np.linspace(-0.5, 0.5, 100)
    plt.hist(word_attributions_dict[word]["LABEL_0"], bins, alpha=0.5, label='No Risk')
    plt.hist(word_attributions_dict[word]["LABEL_1"], bins, alpha=0.5, label='Low Risk')
    plt.hist(word_attributions_dict[word]["LABEL_2"], bins, alpha=0.5, label='Moderate Risk')
    plt.hist(word_attributions_dict[word]["LABEL_3"], bins, alpha=0.5, label='Severe Risk')
    plt.legend(loc='upper right')
    plt.show()

In [198]:
cls_explainer.visualize(true_class=3)

# <a id='toc4_'></a>[LIME](#toc0_)

In [123]:
import lime

In [124]:
from lime.lime_text import LimeTextExplainer

In [179]:
def predictor(input_text):
    inputs = tokenizer.encode(input_text, return_tensors="pt")

    # Get the attention weights from the last layer
    with torch.no_grad():
        outputs = model(inputs)

    probs = torch.softmax(outputs.logits, dim=1).detach().numpy()
    return probs

In [190]:
class_names = ["No Risk","Low Risk","Moderate Risk","Severe Risk"]
explainer = LimeTextExplainer(class_names=class_names)

In [192]:
exp = explainer.explain_instance([input_text][0],predictor, num_features=20, num_samples=2000)

TypeError: TextEncodeInput must be Union[TextInputSequence, Tuple[InputSequence, InputSequence]]

In [132]:
exp.show_in_notebook(text=input_text)

NameError: name 'exp' is not defined

# <a id='toc5_'></a>[BERTViz](#toc0_)

In [177]:
short_text = "I had the gun in my mouth pointed, I think, at my brain stem. I had both index fingers on the trigger and I wanted to pull harder."
# short_text = "I don't know why but I couldn't. I was breathing so hard. I feel so scared. I don't know what I'm going to do."
# short_text = "I guess I have to face another week somehow. I put my laundry in the wash. I don't know what I'm doing anymore."
# short_text = "Maybe I'll try and seal a plastic bag over my head instead. It's less violent and its not something I have to actively do. I can just lay there."
# short_text = "I don't know what I'm going to do. I don't think I can handle another week. I'm so done."
# short_text = "I had my last therapist appointment today. She told me that while she doesn't want me to die, and she wishes I'd give more time to doctors and meds and whatever."
# short_text = "I don't have the energy or the will for that anymore. I just can't. I'm so tired. I have to be done. I just have to find a way that I can handle. I'm sorry for this pointless post."

short_token = tokenizer.encode(short_text, return_tensors="pt")

# Get the attention weights from the last layer
with torch.no_grad():
    short_output = model(short_token)

In [178]:
from bertviz import head_view
head_view(short_output[-1], tokenizer.convert_ids_to_tokens(short_token[0]))

<IPython.core.display.Javascript object>